In [156]:
%matplotlib inline

Generation of Questions with a seq2seq network 
*************************************************************




::

    [KEY: > input, = target, < output]

   

This is made possible by the simple but powerful idea of the `sequence
to sequence network <http://arxiv.org/abs/1409.3215>`__, in which two
recurrent neural networks work together to transform one sequence to
another. An encoder network condenses an input sequence into a vector,
and a decoder network unfolds that vector into a new sequence.

.. figure:: /_static/img/seq-seq-images/seq2seq.png
   :alt:

To improve upon this model we'll use an `attention
mechanism <https://arxiv.org/abs/1409.0473>`__, which lets the decoder
learn to focus over a specific range of the input sequence.

**Requirements**



In [157]:
from __future__ import unicode_literals, print_function, division
from io import open
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Loading data files
===================

The data for this project is a set of many thousands of sentence pairs, broken down into two main groups i.e agreement and no agreement and are present in the dataset folder of the project



Similar to the character encoding used in the character-level RNN
tutorials, we will be representing each word in a language as a one-hot
vector, or giant vector of zeros except for a single one (at the index
of the word). Compared to the dozens of characters that might exist in a
language, there are many many more words, so the encoding vector is much
larger. We will however cheat a bit and trim the data to only use a few
thousand words per language.

.. figure:: /_static/img/seq-seq-images/word-encoding.png
   :alt:





We'll need a unique index per word to use as the inputs and targets of
the networks later. To keep track of all this we will use a helper class
called ``Lang`` which has word → index (``word2index``) and index → word
(``index2word``) dictionaries, as well as a count of each word
``word2count`` to use to later replace rare words.




In [158]:
SOS_token = 0
IDENT_TOKEN = -1
QUEST_TOKEN = -1
EOS_TOKEN =1


class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

we will make evertything lower case adn trim most punctuation.




In [159]:


# Lowercase, trim, and remove non-letter characters


def normalizeString(s):
    s = (s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    return s

To read the data file we will split the file into lines, and then split
lines into pairs




In [160]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open('./../data/agreement_data/train_data.txt' ,).\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

The maximum length of each sentence has been set to a 100 words.



In [161]:
MAX_LENGTH = 100



def filterPairs(pairs):
    return [pair for pair in pairs]

The full process for preparing the data is:

-  Read text file and split into lines, split lines into pairs
-  Normalize text, filter by length and content
-  Make word lists from sentences in pairs




In [162]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs


input_lang, output_lang, pairs = prepareData('out', 'inp', True)
IDENT_TOKEN = input_lang.word2index["ident"]
QUEST_TOKEN = input_lang.word2index["quest"]
print(random.choice(pairs))

Reading lines...
Read 435500 sentence pairs
Trimmed to 435500 sentence pairs
Counting words...
Counted words:
inp 54
out 52
['your bird around your birds does call her cats around your rabbits quest', 'does your bird around your birds call her cats around your rabbits']


The Seq2Seq Model
=================

A Recurrent Neural Network, or RNN, is a network that operates on a
sequence and uses its own output as input for subsequent steps.

A `Sequence to Sequence network <http://arxiv.org/abs/1409.3215>`__, or
seq2seq network, or `Encoder Decoder
network <https://arxiv.org/pdf/1406.1078v3.pdf>`__, is a model
consisting of two RNNs called the encoder and decoder. The encoder reads
an input sequence and outputs a single vector, and the decoder reads
that vector to produce an output sequence.

.. figure:: /_static/img/seq-seq-images/seq2seq.png
   :alt:

Unlike sequence prediction with a single RNN, where every input
corresponds to an output, the seq2seq model frees us from sequence
length and order, which makes it ideal for translation between two
languages.

With a seq2seq model the encoder creates a single vector which, in the
ideal case, encodes the "meaning" of the input sequence into a single
vector — a single point in some N dimensional space of sentences.




The Encoder
-----------

The encoder of a seq2seq network is a RNN that outputs some value for
every word from the input sentence. For every input word the encoder
outputs a vector and a hidden state, and uses the hidden state for the
next input word.

.. figure:: /_static/img/seq-seq-images/encoder-network.png
   :alt:





In [163]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)

The Decoder
-----------

The decoder is another RNN that takes the encoder output vector(s) and
outputs a sequence of words to create the translation.




Simple Decoder
^^^^^^^^^^^^^^

In the simplest seq2seq decoder we use only last output of the encoder.
This last output is sometimes called the *context vector* as it encodes
context from the entire sequence. This context vector is used as the
initial hidden state of the decoder.

At every step of decoding, the decoder is given an input token and
hidden state. The initial input token is the start-of-string ``<SOS>``
token, and the first hidden state is the context vector (the encoder's
last hidden state).

.. figure:: /_static/img/seq-seq-images/decoder-network.png
   :alt:





In [164]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)

Attention Decoder
^^^^^^^^^^^^^^^^^

If only the context vector is passed betweeen the encoder and decoder,
that single vector carries the burden of encoding the entire sentence.

Attention allows the decoder network to "focus" on a different part of
the encoder's outputs for every step of the decoder's own outputs. First
we calculate a set of *attention weights*. These will be multiplied by
the encoder output vectors to create a weighted combination. The result
(called ``attn_applied`` in the code) should contain information about
that specific part of the input sequence, and thus help the decoder
choose the right output words.

.. figure:: https://i.imgur.com/1152PYf.png
   :alt:

Calculating the attention weights is done with another feed-forward
layer ``attn``, using the decoder's input and hidden state as inputs.
Because there are sentences of all sizes in the training data, to
actually create and train this layer we have to choose a maximum
sentence length (input length, for encoder outputs) that it can apply
to. Sentences of the maximum length will use all the attention weights,
while shorter sentences will only use the first few.

.. figure:: /_static/img/seq-seq-images/attention-decoder-network.png
   :alt:





In [165]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding(self.output_size, self.hidden_size)
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)
        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))

        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)



Training
========

Preparing Training Data
-----------------------

To train, for each pair we will need an input tensor (indexes of the
words in the input sentence) and target tensor (indexes of the words in
the target sentence). While creating these vectors we will append the
EOS token to both sequences.




In [166]:
def indexesFromSentence(lang, sentence):
    return [lang.word2index[word] for word in sentence.split(' ')]


def tensorFromSentence(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    indexes.append(EOS_TOKEN)
        
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


def tensorsFromPair(pair):
    input_tensor = tensorFromSentence(input_lang, pair[0])
    target_tensor = tensorFromSentence(output_lang, pair[1])
    return (input_tensor, target_tensor)

Training the Model
------------------

To train we run the input sentence through the encoder, and keep track
of every output and the latest hidden state. Then the decoder is given
the ``<SOS>`` token as its first input, and the last hidden state of the
encoder as its first hidden state.

"Teacher forcing" is the concept of using the real target outputs as
each next input, instead of using the decoder's guess as the next input.
Using teacher forcing causes it to converge faster but `when the trained
network is exploited, it may exhibit
instability <http://minds.jacobs-university.de/sites/default/files/uploads/papers/ESNTutorialRev.pdf>`__.

You can observe outputs of teacher-forced networks that read with
coherent grammar but wander far from the correct translation -
intuitively it has learned to represent the output grammar and can "pick
up" the meaning once the teacher tells it the first few words, but it
has not properly learned how to create the sentence from the translation
in the first place.

Because of the freedom PyTorch's autograd gives us, we can randomly
choose to use teacher forcing or not with a simple if statement. Turn
``teacher_forcing_ratio`` up to use more of it.




In [167]:
tensorsFromPair(pairs[0])

C
[2, 3, 4, 5, 6]
1
C
[2, 3, 4, 5]
1


(tensor([[2],
         [3],
         [4],
         [5],
         [6],
         [1]]), tensor([[2],
         [3],
         [4],
         [5],
         [1]]))

In [168]:
teacher_forcing_ratio = 0.5


def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == IDENT_TOKEN or decoder_input.item() == QUEST_TOKEN or decoder_input.item()== EOS_TOKEN:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

This is a helper function to print time elapsed and estimated time
remaining given the current time and progress %.




In [169]:
import time
import math


def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))

The whole training process looks like this:

-  Start a timer
-  Initialize optimizers and criterion
-  Create set of training pairs
-  Start empty losses array for plotting

Then we call ``train`` many times and occasionally print the progress (%
of examples, time so far, estimated time) and average loss.




In [170]:
def trainIters(encoder, decoder, n_iters, print_every=1000, plot_every=100, learning_rate=0.01):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    training_pairs = [tensorsFromPair(random.choice(pairs))
                      for i in range(n_iters)]
    criterion = nn.NLLLoss()

    for iter in range(1, n_iters + 1):
        training_pair = training_pairs[iter - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train(input_tensor, target_tensor, encoder,
                     decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss
        plot_loss_total += loss

        if iter % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                         iter, iter / n_iters * 100, print_loss_avg))

        if iter % plot_every == 0:
            plot_loss_avg = plot_loss_total / plot_every
            plot_losses.append(plot_loss_avg)
            plot_loss_total = 0

    showPlot(plot_losses)

Plotting results
----------------

Plotting is done with matplotlib, using the array of loss values
``plot_losses`` saved while training.




In [171]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np


def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)

Evaluation
==========

Evaluation is mostly the same as training, but there are no targets so
we simply feed the decoder's predictions back to itself for each step.
Every time it predicts a word we add it to the output string, and if it
predicts the EOS token we stop there. We also store the decoder's
attention outputs for display later.




In [172]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(input_lang, sentence)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == IDENT_TOKEN :
                decoded_words.append('<IDENT>')
                break
            elif topi.item() == QUEST_TOKEN :
                decoded_words.append('<QUEST>')
                break
            elif topi.item() == EOS_TOKEM :
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(output_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]

We can evaluate random sentences from the training set and print out the
input, target, and output to make some subjective quality judgements:




In [173]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')

Training and Evaluating
=======================



In [174]:
class TheModelClass(nn.Module):
    def __init__(self):
        super(TheModelClass, self).__init__()
        self.conv1 = nn.Conv2d(3, 6, 5)
        self.pool = nn.MaxPool2d(2, 2)
        self.conv2 = nn.Conv2d(6, 16, 5)
        self.fc1 = nn.Linear(16 * 5 * 5, 120)
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, 10)

    def forward(self, x):
        x = self.pool(F.relu(self.conv1(x)))
        x = self.pool(F.relu(self.conv2(x)))
        x = x.view(-1, 16 * 5 * 5)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

# Initialize model
model = TheModelClass()

# Initialize optimizer
optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)

# Print model's state_dict
print("Model's state_dict:")
for param_tensor in model.state_dict():
    print(param_tensor, "\t", model.state_dict()[param_tensor].size())

# Print optimizer's state_dict
print("Optimizer's state_dict:")
for var_name in optimizer.state_dict():
    print(var_name, "\t", optimizer.state_dict()[var_name])


Model's state_dict:
conv1.weight 	 torch.Size([6, 3, 5, 5])
conv1.bias 	 torch.Size([6])
conv2.weight 	 torch.Size([16, 6, 5, 5])
conv2.bias 	 torch.Size([16])
fc1.weight 	 torch.Size([120, 400])
fc1.bias 	 torch.Size([120])
fc2.weight 	 torch.Size([84, 120])
fc2.bias 	 torch.Size([84])
fc3.weight 	 torch.Size([10, 84])
fc3.bias 	 torch.Size([10])
Optimizer's state_dict:
state 	 {}
param_groups 	 [{'momentum': 0.9, 'params': [140310787575312, 140310949050048, 140310949048968, 140310949049040, 140310949048608, 140310930288928, 140310930292312, 140310930290008, 140310930290224, 140310949435864], 'lr': 0.001, 'nesterov': False, 'weight_decay': 0, 'dampening': 0}]


In [175]:
model_exists = False
if model_exists :
    model = torch.load("no_agreement.pt")
    model.eval()

In [176]:
hidden_size = 256
counter=1
while(counter == 1 ):
    name = "aagreement_"+str(counter)+".pt"
    print(name)
    
    encoder1 = EncoderRNN(input_lang.n_words, hidden_size).to(device)
    attn_decoder1 = AttnDecoderRNN(hidden_size, output_lang.n_words, dropout_p=0.1).to(device)
    trainIters(encoder1, attn_decoder1, 75000, print_every=50)
    
    torch.save(model.state_dict,name)   
    counter+=1

aagreement_1.pt
C
[7, 23, 21, 45, 7, 36, 6]
1
C
[18, 7, 22, 43, 7, 35]
1
C
[19, 25, 37, 22, 3, 9, 29, 4, 24, 6]
1
C
[2, 19, 24, 36, 21, 4, 6, 28, 23]
1
C
[14, 33, 4, 45, 14, 36, 39, 19, 33, 4, 10, 38]
1
C
[14, 32, 2, 43, 14, 35, 37, 19, 32, 2, 9]
1
C
[22, 13, 4, 41, 19, 33, 39, 9, 40, 22, 13, 6]
1
C
[2, 21, 12, 39, 19, 32, 37, 6, 38, 21, 12]
1
C
[19, 11, 48, 22, 30, 9, 12, 38]
1
C
[19, 10, 46, 21, 29, 6, 11]
1
C
[14, 27, 9, 41, 19, 34, 46, 19, 34, 38]
1
C
[14, 26, 6, 39, 19, 33, 44, 19, 33]
1
C
[22, 11, 53, 22, 36, 9, 44, 22, 20, 48, 22, 33, 38]
1
C
[21, 10, 51, 21, 35, 6, 42, 21, 20, 46, 21, 32]
1
C
[26, 18, 39, 7, 3, 9, 24, 9, 10, 38]
1
C
[25, 17, 37, 7, 4, 6, 23, 6, 9]
1
C
[22, 3, 47, 22, 20, 9, 44, 2, 3, 38]
1
C
[21, 4, 45, 21, 20, 6, 42, 3, 4]
1
C
[26, 11, 4, 43, 2, 28, 6]
1
C
[2, 25, 10, 41, 3, 27]
1
C
[22, 25, 37, 9, 29, 4, 43, 2, 23, 38]
1
C
[21, 24, 36, 6, 28, 2, 41, 3, 22]
1
C
[14, 3, 4, 41, 7, 33, 39, 14, 33, 4, 12, 6]
1
C
[2, 14, 4, 39, 7, 32, 37, 14, 32, 2, 11]
1
C
[7, 13,

C
[3, 34, 48, 25, 22, 2, 38, 25, 34]
1
C
[19, 34, 50, 7, 34, 16, 12, 38]
1
C
[19, 33, 48, 7, 33, 13, 11]
1
C
[7, 18, 49, 7, 20, 4, 40, 7, 25, 37, 14, 33, 9, 12, 6]
1
C
[2, 7, 17, 47, 7, 20, 38, 7, 24, 36, 14, 32, 6, 11]
1
C
[19, 35, 53, 19, 20, 4, 44, 2, 20, 39, 16, 44, 19, 30, 6]
1
C
[2, 19, 34, 51, 19, 20, 42, 3, 20, 37, 13, 42, 19, 29]
1
C
[22, 3, 39, 2, 15, 21, 17, 4, 17, 6]
1
C
[2, 21, 4, 37, 3, 15, 18, 16, 16]
1
C
[22, 25, 39, 9, 10, 4, 42, 22, 27, 38]
1
C
[21, 24, 37, 6, 9, 2, 40, 21, 26]
1
C
[2, 30, 50, 26, 13, 21, 24, 38]
1
C
[3, 29, 48, 25, 12, 18, 23]
1
C
[19, 25, 50, 14, 18, 4, 17, 38]
1
C
[19, 24, 48, 14, 17, 2, 16]
1
C
[19, 27, 48, 19, 23, 4, 41, 22, 23, 39, 21, 42, 22, 32, 38]
1
C
[19, 26, 46, 19, 22, 2, 39, 21, 22, 37, 18, 40, 21, 31]
1
C
[19, 8, 9, 40, 19, 11, 48, 19, 11, 38]
1
C
[19, 8, 6, 38, 19, 10, 46, 19, 10]
1
C
[14, 8, 39, 22, 34, 21, 5, 9, 5, 6]
1
C
[6, 14, 8, 37, 21, 33, 18, 5, 5]
1
C
[14, 13, 37, 2, 11, 4, 17, 9, 5, 38]
1
C
[14, 12, 36, 3, 10, 2, 16, 6, 5]
1


[26, 8, 50, 26, 3, 4, 29, 38]
1
C
[25, 8, 48, 25, 4, 2, 28]
1
C
[2, 27, 4, 42, 2, 32, 37, 14, 32, 21, 24, 6]
1
C
[2, 3, 26, 40, 3, 31, 36, 14, 31, 18, 23]
1
C
[7, 3, 4, 40, 19, 13, 39, 4, 40, 19, 35, 38]
1
C
[7, 4, 2, 38, 19, 12, 37, 2, 38, 19, 34]
1
C
[14, 31, 49, 19, 31, 16, 5, 38]
1
C
[14, 30, 47, 19, 30, 13, 5]
1
C
[14, 34, 21, 42, 14, 8, 6]
1
C
[18, 14, 33, 40, 14, 8]
1
C
[7, 11, 47, 14, 18, 9, 41, 7, 31, 6]
1
C
[6, 7, 10, 45, 14, 17, 39, 7, 30]
1
C
[7, 35, 49, 7, 20, 9, 10, 38]
1
C
[7, 34, 47, 7, 20, 6, 9]
1
C
[22, 8, 39, 22, 23, 21, 29, 9, 29, 38]
1
C
[21, 8, 37, 21, 22, 18, 28, 6, 28]
1
C
[7, 33, 39, 22, 8, 9, 10, 4, 10, 38]
1
C
[7, 32, 37, 21, 8, 6, 9, 2, 9]
1
C
[14, 25, 4, 44, 14, 32, 48, 14, 31, 38]
1
C
[14, 24, 2, 42, 14, 31, 46, 14, 30]
1
C
[26, 3, 4, 45, 26, 33, 39, 4, 45, 7, 33, 6]
1
C
[2, 25, 4, 43, 25, 32, 37, 2, 43, 7, 32]
1
C
[22, 18, 39, 22, 35, 9, 10, 4, 10, 38]
1
C
[21, 17, 37, 21, 34, 6, 9, 2, 9]
1
C
[19, 13, 9, 42, 14, 27, 51, 19, 36, 6]
1
C
[6, 19, 12, 40, 14, 

C
[2, 33, 4, 42, 14, 36, 48, 14, 32, 38]
1
C
[3, 32, 2, 40, 14, 35, 46, 14, 31]
1
C
[2, 11, 9, 40, 7, 34, 46, 2, 15, 6]
1
C
[6, 3, 10, 38, 7, 33, 44, 3, 15]
1
C
[26, 18, 4, 40, 26, 18, 52, 26, 23, 38]
1
C
[25, 17, 2, 38, 25, 17, 50, 25, 22]
1
C
[19, 18, 9, 44, 7, 18, 6]
1
C
[6, 19, 17, 42, 7, 17]
1
C
[2, 27, 4, 43, 7, 3, 39, 2, 23, 21, 29, 38]
1
C
[3, 26, 2, 41, 7, 4, 37, 3, 22, 18, 28]
1
C
[2, 33, 50, 2, 25, 9, 43, 14, 15, 38]
1
C
[3, 32, 48, 3, 24, 6, 41, 14, 15]
1
C
[14, 11, 47, 7, 20, 9, 10, 38]
1
C
[14, 10, 45, 7, 20, 6, 9]
1
C
[26, 25, 37, 4, 12, 4, 41, 26, 11, 51, 22, 26, 11, 38]
1
C
[25, 24, 36, 2, 11, 2, 39, 25, 10, 49, 21, 25, 10]
1
C
[7, 3, 53, 7, 15, 4, 45, 7, 15, 53, 19, 23, 6]
1
C
[2, 7, 4, 51, 7, 15, 43, 7, 15, 51, 19, 22]
1
C
[19, 27, 39, 19, 18, 4, 12, 4, 24, 38]
1
C
[19, 26, 37, 19, 17, 2, 11, 2, 23]
1
C
[7, 18, 4, 44, 7, 8, 37, 4, 44, 19, 8, 38]
1
C
[7, 17, 2, 42, 7, 8, 36, 2, 42, 19, 8]
1
C
[2, 33, 37, 2, 33, 4, 5, 4, 5, 6]
1
C
[2, 3, 32, 36, 3, 32, 2, 5, 5]
1
C
[2,

C
[6, 19, 24, 37, 6, 11, 5]
1
C
[7, 33, 37, 7, 31, 21, 10, 9, 12, 6]
1
C
[6, 7, 32, 36, 7, 30, 18, 9, 11]
1
C
[26, 35, 37, 26, 25, 9, 12, 4, 12, 6]
1
C
[2, 25, 34, 36, 25, 24, 6, 11, 11]
1
C
[14, 18, 47, 14, 34, 4, 43, 26, 18, 37, 14, 36, 21, 17, 6]
1
C
[2, 14, 17, 45, 14, 33, 41, 25, 17, 36, 14, 35, 18, 16]
1
C
[7, 15, 16, 40, 19, 3, 6]
1
C
[13, 7, 15, 38, 19, 4]
1
C
[26, 27, 39, 22, 28, 16, 24, 9, 24, 6]
1
C
[6, 25, 26, 37, 21, 27, 13, 23, 23]
1
C
[26, 3, 53, 26, 23, 4, 5, 38]
1
C
[25, 4, 51, 25, 22, 2, 5]
1
C
[2, 18, 37, 2, 3, 4, 29, 4, 5, 6]
1
C
[2, 3, 17, 36, 3, 4, 2, 28, 5]
1
C
[19, 34, 21, 42, 22, 31, 6]
1
C
[18, 19, 33, 40, 21, 30]
1
C
[26, 8, 51, 26, 23, 9, 45, 26, 8, 51, 14, 30, 6]
1
C
[6, 25, 8, 49, 25, 22, 43, 25, 8, 49, 14, 29]
1
C
[26, 25, 46, 26, 34, 4, 41, 26, 31, 37, 21, 41, 26, 35, 38]
1
C
[25, 24, 44, 25, 33, 2, 39, 25, 30, 36, 18, 39, 25, 34]
1
C
[22, 33, 46, 2, 8, 9, 17, 38]
1
C
[21, 32, 44, 3, 8, 6, 16]
1
C
[26, 3, 50, 26, 36, 4, 40, 26, 25, 39, 9, 40, 19, 25, 6]


...

C
[25, 24, 2, 43, 25, 30, 36, 13, 40, 25, 24]
1
C
[14, 31, 37, 16, 17, 16, 43, 7, 15, 38]
1
C
[14, 30, 36, 13, 16, 13, 41, 7, 15]
1
C
[19, 8, 39, 2, 20, 16, 12, 9, 24, 6]
1
C
[6, 19, 8, 37, 3, 20, 13, 11, 23]
1
C
[7, 18, 47, 7, 36, 4, 42, 22, 27, 47, 7, 18, 38]
1
C
[7, 17, 45, 7, 35, 2, 40, 21, 26, 45, 7, 17]
1
C
[2, 27, 37, 7, 36, 16, 12, 4, 10, 38]
1
C
[3, 26, 36, 7, 35, 13, 11, 2, 9]
1
C
[7, 11, 9, 10, 6]
1
C
[6, 7, 10, 9]
1
C
[22, 11, 53, 26, 34, 9, 45, 26, 27, 38]
1
C
[21, 10, 51, 25, 33, 6, 43, 25, 26]
1
C
[7, 13, 49, 7, 31, 4, 17, 38]
1
C
[7, 12, 47, 7, 30, 2, 16]
1
C
[22, 27, 39, 22, 30, 21, 17, 9, 24, 6]
1
C
[6, 21, 26, 37, 21, 29, 18, 16, 23]
1
C
[19, 32, 47, 19, 20, 16, 5, 38]
1
C
[19, 31, 45, 19, 20, 13, 5]
1
C
[19, 18, 39, 4, 29, 9, 29, 6]
1
C
[6, 19, 17, 37, 2, 28, 28]
1
C
[14, 8, 48, 14, 20, 4, 41, 14, 20, 37, 19, 35, 4, 10, 38]
1
C
[14, 8, 46, 14, 20, 2, 39, 14, 20, 36, 19, 34, 2, 9]
1
C
[19, 33, 4, 40, 22, 13, 39, 19, 15, 16, 10, 38]
1
C
[19, 32, 2, 38, 21, 12, 37, 19,

C
[14, 27, 39, 22, 3, 4, 24, 9, 24, 38]
1
C
[14, 26, 37, 21, 4, 2, 23, 6, 23]
1
C
[19, 28, 47, 19, 8, 16, 12, 38]
1
C
[19, 27, 45, 19, 8, 13, 11]
1
C
[22, 35, 9, 44, 2, 18, 6]
1
C
[6, 21, 34, 42, 3, 17]
1
C
[2, 8, 4, 41, 2, 8, 38]
1
C
[3, 8, 2, 39, 3, 8]
1
C
[22, 35, 39, 14, 32, 21, 29, 9, 29, 6]
1
C
[6, 21, 34, 37, 14, 31, 18, 28, 28]
1
C
[7, 36, 39, 16, 12, 16, 24, 38]
1
C
[7, 35, 37, 13, 11, 13, 23]
1
C
[22, 8, 51, 22, 15, 4, 41, 19, 34, 51, 19, 34, 6]
1
C
[2, 21, 8, 49, 21, 15, 39, 19, 33, 49, 19, 33]
1
C
[26, 13, 9, 44, 26, 31, 49, 26, 32, 6]
1
C
[6, 25, 12, 42, 25, 30, 47, 25, 31]
1
C
[26, 27, 4, 45, 26, 8, 37, 2, 20, 21, 12, 6]
1
C
[2, 25, 26, 43, 25, 8, 36, 3, 20, 18, 11]
1
C
[26, 13, 4, 43, 26, 32, 39, 2, 11, 4, 12, 6]
1
C
[2, 25, 12, 41, 25, 31, 37, 3, 10, 2, 11]
1
C
[19, 8, 37, 2, 3, 9, 12, 9, 10, 38]
1
C
[19, 8, 36, 3, 4, 6, 11, 6, 9]
1
C
[14, 3, 37, 14, 3, 4, 29, 9, 43, 2, 20, 38]
1
C
[14, 4, 36, 14, 4, 2, 28, 6, 41, 3, 20]
1
C
[22, 27, 51, 22, 34, 4, 44, 26, 34, 51, 22, 2

C
[6, 7, 32, 37, 3, 17, 2, 9, 9]
1
C
[26, 13, 46, 26, 32, 4, 41, 14, 34, 52, 26, 3, 6]
1
C
[2, 25, 12, 44, 25, 31, 39, 14, 33, 50, 25, 4]
1
C
[26, 31, 53, 19, 33, 21, 12, 38]
1
C
[25, 30, 51, 19, 32, 18, 11]
1
C
[26, 25, 39, 26, 23, 16, 5, 4, 5, 6]
1
C
[2, 25, 24, 37, 25, 22, 13, 5, 5]
1
C
[19, 3, 49, 19, 28, 4, 43, 22, 3, 6]
1
C
[2, 19, 4, 47, 19, 27, 41, 21, 4]
1
C
[14, 34, 37, 21, 12, 21, 41, 14, 34, 38]
1
C
[14, 33, 36, 18, 11, 18, 39, 14, 33]
1
C
[7, 30, 51, 26, 34, 21, 10, 38]
1
C
[7, 29, 49, 25, 33, 18, 9]
1
C
[22, 18, 37, 22, 28, 16, 17, 9, 10, 6]
1
C
[6, 21, 17, 36, 21, 27, 13, 16, 9]
1
C
[7, 3, 47, 7, 28, 4, 42, 7, 3, 47, 7, 3, 6]
1
C
[2, 7, 4, 45, 7, 27, 40, 7, 4, 45, 7, 4]
1
C
[19, 25, 50, 19, 15, 4, 44, 14, 15, 46, 19, 15, 6]
1
C
[2, 19, 24, 48, 19, 15, 42, 14, 15, 44, 19, 15]
1
C
[7, 33, 47, 7, 23, 4, 40, 7, 33, 47, 22, 34, 38]
1
C
[7, 32, 45, 7, 22, 2, 38, 7, 32, 45, 21, 33]
1
C
[2, 18, 39, 2, 18, 4, 17, 9, 12, 6]
1
C
[6, 3, 17, 37, 3, 17, 2, 16, 11]
1
C
[7, 34, 16, 41, 

C
[19, 25, 37, 2, 18, 9, 29, 4, 24, 38]
1
C
[19, 24, 36, 3, 17, 6, 28, 2, 23]
1
C
[7, 8, 39, 4, 17, 9, 17, 6]
1
C
[6, 7, 8, 37, 2, 16, 16]
1
C
[22, 25, 37, 7, 25, 9, 29, 9, 24, 38]
1
C
[21, 24, 36, 7, 24, 6, 28, 6, 23]
1
C
[22, 13, 4, 42, 22, 30, 39, 19, 33, 4, 12, 38]
1
C
[21, 12, 2, 40, 21, 29, 37, 19, 32, 2, 11]
1
C
[14, 13, 4, 41, 14, 35, 37, 14, 32, 16, 24, 38]
1
C
[14, 12, 2, 39, 14, 34, 36, 14, 31, 13, 23]
1
C
[22, 25, 49, 22, 30, 4, 44, 14, 13, 39, 22, 30, 21, 12, 38]
1
C
[21, 24, 47, 21, 29, 2, 42, 14, 12, 37, 21, 29, 18, 11]
1
C
[2, 31, 52, 7, 18, 21, 24, 38]
1
C
[3, 30, 50, 7, 17, 18, 23]
1
C
[19, 3, 39, 4, 5, 9, 45, 22, 3, 38]
1
C
[19, 4, 37, 2, 5, 6, 43, 21, 4]
1
C
[14, 33, 47, 14, 31, 9, 41, 14, 34, 52, 14, 33, 38]
1
C
[14, 32, 45, 14, 30, 6, 39, 14, 33, 50, 14, 32]
1
C
[14, 33, 53, 26, 34, 9, 29, 38]
1
C
[14, 32, 51, 25, 33, 6, 28]
1
C
[7, 28, 51, 19, 25, 21, 5, 38]
1
C
[7, 27, 49, 19, 24, 18, 5]
1
C
[14, 18, 47, 19, 28, 9, 17, 38]
1
C
[14, 17, 45, 19, 27, 6, 16]
1
C
[2,

KeyboardInterrupt: 

In [ ]:
evaluateRandomly(encoder1, attn_decoder1)

Visualizing Attention
---------------------

A useful property of the attention mechanism is its highly interpretable
outputs. Because it is used to weight specific encoder outputs of the
input sequence, we can imagine looking where the network is focused most
at each time step.

You could simply run ``plt.matshow(attentions)`` to see attention output
displayed as a matrix, with the columns being input steps and rows being
output steps:




In [45]:
output_words, attentions = evaluate(
    encoder1, attn_decoder1, "our cats do read quest")
plt.matshow(attentions.numpy())

For a better viewing experience we will do the extra work of adding axes
and labels:




In [73]:
def showAttention(input_sentence, output_words, attentions):
    # Set up figure with colorbar
    fig = plt.figure()
    ax = fig.add_subplot(111)
    cax = ax.matshow(attentions.numpy(), cmap='bone')
    fig.colorbar(cax)

    # Set up axes
    ax.set_xticklabels([''] + input_sentence.split(' ') +
                       ['<end>'], rotation=90)
    ax.set_yticklabels([''] + output_words)

    # Show label at every tick
    ax.xaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))

    plt.show()
    fig.savefig(input_sentence+'.png')


def evaluateAndShowAttention(input_sentence):
    output_words, attentions = evaluate(
        encoder1, attn_decoder1, input_sentence)
    print('input =', input_sentence)
    print('output =', ' '.join(output_words))
    showAttention(input_sentence, output_words, attentions)


evaluateAndShowAttention("my cats by my yaks dont smile quest")



input = my cats by my yaks dont smile quest
output = dont my cats by my yaks smile dont smile read smile smile sleep smile my cats smile dont smile read smile confuse my yaks that dont smile do irritate my cats that dont smile do smile read smile irritate my seals that dont smile do irritate my cats that dont smile do irritate my yaks that dont smile do confuse my cats that dont smile do irritate my seals that dont smile do confuse my yaks that dont smile do irritate my cats that dont smile do confuse my seals that dont smile do irritate my monkey that dont smile
